# Naver Movie Review Sentiment Analysis   
* 작성자 : 김가윤   
* 일시 : 2022-05-12 ~   
* 코드 참고 : https://wikidocs.net/44249 , https://github.com/BlueWhaleKo/NLP_sentiment_classification/blob/master/LSTM/LSTM.ipynb   
* 데이터 : https://github.com/e9t/nsmc/   

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import re
#import urllib.request
from konlpy.tag import Okt
from tqdm import tqdm

In [2]:
import torch.nn as nn
import torch
from torch.autograd import Variable
import torch.nn.functional as F
import random

## 데이터 다운로드 및 분석

In [3]:
#urllib.request.urlretrieve("https://raw.githubusercontent.com/e9t/nsmc/master/ratings_train.txt", filename="ratings_train.txt")
#urllib.request.urlretrieve("https://raw.githubusercontent.com/e9t/nsmc/master/ratings_test.txt", filename="ratings_test.txt")

In [4]:
def read_txt(path_to_file): # 데이터 읽어오기
    txt_ls = []
    label_ls = []

    with open(path_to_file) as f:
        for i, line in enumerate(f.readlines()[1:]):
            id_num, txt, label = line.split('\t')
            txt_ls.append(txt)
            label_ls.append(int(label.replace('\n','')))
    return txt_ls, label_ls##

In [5]:
from collections import Counter # 데이터 개수를 셀 때 유용함

In [6]:
#x_train, y_train = read_txt('ratings_train.txt') # 원래 스트링으로 된 리스트임
#x_test, y_test = read_txt('ratings_test.txt')

#x_train = [x.split() for x in x_train]
#x_test = [x.split() for x in x_test]

In [7]:
train_data = pd.read_table('ratings_train.txt')
test_data = pd.read_table('ratings_test.txt')

In [8]:
print('훈련용 리뷰 개수 :',len(train_data)) # 훈련용 리뷰 개수 출력

훈련용 리뷰 개수 : 150000


In [9]:
train_data[:5] # 상위 5개 출력

id                                           document  label
0   9976970                                아 더빙.. 진짜 짜증나네요 목소리      0
1   3819312                  흠...포스터보고 초딩영화줄....오버연기조차 가볍지 않구나      1
2  10265843                                  너무재밓었다그래서보는것을추천한다      0
3   9045019                      교도소 이야기구먼 ..솔직히 재미는 없다..평점 조정      0
4   6483659  사이몬페그의 익살스런 연기가 돋보였던 영화!스파이더맨에서 늙어보이기만 했던 커스틴 ...      1

id 필요없고, document가 긍, 부를 나타내도록 학습해야함, 띄어쓰기 되지 않아도 이해되는 한국어 특성 나타남(index 2)

In [10]:
print('테스트용 리뷰 개수 :',len(test_data))

테스트용 리뷰 개수 : 50000


In [11]:
test_data[:5]

id                                           document  label
0  6270596                                                굳 ㅋ      1
1  9274899                               GDNTOPCLASSINTHECLUB      0
2  8544678             뭐야 이 평점들은.... 나쁘진 않지만 10점 짜리는 더더욱 아니잖아      0
3  6825595                   지루하지는 않은데 완전 막장임... 돈주고 보기에는....      0
4  6723715  3D만 아니었어도 별 다섯 개 줬을텐데.. 왜 3D로 나와서 제 심기를 불편하게 하죠??      0

## 데이터 정제하기

In [12]:
train_data['document'].nunique(), train_data['label'].nunique()

(146182, 2)

`nunique()`는 데이터에 고유값들의 수를 출력해주는 함수, 튜플에 2가 오는 이유는 긍, 부 레이블 종류가 2개 이기 때문이다.

In [13]:
# document 열의 중복 제거
train_data.drop_duplicates(subset=['document'], inplace=True)

In [14]:
print('총 샘플의 수 :',len(train_data))

총 샘플의 수 : 146183


In [15]:
#train_data['label'].value_counts().plot(kind = 'bar')

kernel dies when plotting the data https://github.com/jupyter/notebook/issues/6219

In [18]:
train_data.groupby('label').size().reset_index(name = 'count')

label  count
0      0  73342
1      1  72841

In [17]:
train_data.isnull().values.any() # null 확인

True

In [19]:
train_data.loc[train_data.document.isnull()]

id document  label
25857  2172111      NaN      1

In [20]:
train_data = train_data.dropna(how = 'any') # Null 값이 존재하는 행 제거

In [21]:
# train_data로부터 한글만 남기고 제거하기 위해서 정규 표현식을 사용
# 한글과 공백을 제외하고 모두 제거
train_data['document'] = train_data['document'].str.replace("[^ㄱ-ㅎㅏ-ㅣ가-힣 ]","")
train_data[:5]

c:\Users\Owner\anaconda3\lib\site-packages\ipykernel_launcher.py:3: FutureWarning: The default value of regex will change from True to False in a future version.
  This is separate from the ipykernel package so we can avoid doing imports until


id                                           document  label
0   9976970                                  아 더빙 진짜 짜증나네요 목소리      0
1   3819312                         흠포스터보고 초딩영화줄오버연기조차 가볍지 않구나      1
2  10265843                                  너무재밓었다그래서보는것을추천한다      0
3   9045019                          교도소 이야기구먼 솔직히 재미는 없다평점 조정      0
4   6483659  사이몬페그의 익살스런 연기가 돋보였던 영화스파이더맨에서 늙어보이기만 했던 커스틴 던...      1

train_data에 공백(whitespace)만 있거나 빈 값을 가진 행이 있다면 Null 값으로 변경하도록 하고, Null 값이 존재하는지 확인

In [22]:
train_data['document'] = train_data['document'].str.replace('^ +', "") # white space 데이터를 empty value로 변경
train_data['document'].replace('', np.nan, inplace=True)
print(train_data.isnull().sum())

c:\Users\Owner\anaconda3\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: The default value of regex will change from True to False in a future version.
  """Entry point for launching an IPython kernel.


id            0
document    789
label         0
dtype: int64


Null 값이 789개나 새로 생김

In [23]:
# drop
train_data = train_data.dropna(how = 'any')
print(len(train_data))

145393


테스트 데이터에도 동시 적용

In [24]:
test_data.drop_duplicates(subset = ['document'], inplace=True) # document 열에서 중복인 내용이 있다면 중복 제거
test_data['document'] = test_data['document'].str.replace("[^ㄱ-ㅎㅏ-ㅣ가-힣 ]","") # 정규 표현식 수행
test_data['document'] = test_data['document'].str.replace('^ +', "") # 공백은 empty 값으로 변경
test_data['document'].replace('', np.nan, inplace=True) # 공백은 Null 값으로 변경
test_data = test_data.dropna(how='any') # Null 값 제거
print('전처리 후 테스트용 샘플의 개수 :',len(test_data))

c:\Users\Owner\anaconda3\lib\site-packages\ipykernel_launcher.py:2: FutureWarning: The default value of regex will change from True to False in a future version.
  
c:\Users\Owner\anaconda3\lib\site-packages\ipykernel_launcher.py:3: FutureWarning: The default value of regex will change from True to False in a future version.
  This is separate from the ipykernel package so we can avoid doing imports until


전처리 후 테스트용 샘플의 개수 : 48852


## 토큰화

토큰화 과정에서 불용어를 제거한다. 불용어는 정의하기 나름인데, 한국어의 조사, 접속사 등의 보편적인 불용어를 사용할 수도 있겠지만 결국 풀고자 하는 문제의 데이터를 지속 검토하면서 계속해서 추가해야 함

In [25]:
stopwords = ['의','가','이','은','들','는','좀','잘','걍','과','도','를','으로','자','에','와','한','하다']

In [26]:
# 형태소 분석기 koNLpy Okt 사용
okt = Okt()
okt.morphs('와 이런 것도 영화라고 차라리 뮤직비디오를 만드는 게 나을 뻔', stem = True)

['오다', '이렇다', '것', '도', '영화', '라고', '차라리', '뮤직비디오', '를', '만들다', '게', '나다', '뻔']

stem = True를 사용하면 일정 수준의 정규화를 수행해주는데, 예를 들어 위의 예제의 결과를 보면 '이런'이 '이렇다'로 변환되었고 '만드는'이 '만들다'로 변환된 것을 알 수 있다

In [27]:
X_train = []
for sentence in tqdm(train_data['document']):
    tokenized_sentence = okt.morphs(sentence, stem=True) # 토큰화
    stopwords_removed_sentence = [word for word in tokenized_sentence if not word in stopwords] # 불용어 제거
    X_train.append(stopwords_removed_sentence)

100%|██████████| 145393/145393 [16:16<00:00, 148.92it/s]


In [30]:
train_data.to_csv(index=False)

'id,document,label\r\n9976970,아 더빙 진짜 짜증나네요 목소리,0\r\n3819312,흠포스터보고 초딩영화줄오버연기조차 가볍지 않구나,1\r\n10265843,너무재밓었다그래서보는것을추천한다,0\r\n9045019,교도소 이야기구먼 솔직히 재미는 없다평점 조정,0\r\n6483659,사이몬페그의 익살스런 연기가 돋보였던 영화스파이더맨에서 늙어보이기만 했던 커스틴 던스트가 너무나도 이뻐보였다,1\r\n5403919,막 걸음마 뗀 세부터 초등학교 학년생인 살용영화ㅋㅋㅋ별반개도 아까움,0\r\n7797314,원작의 긴장감을 제대로 살려내지못했다,0\r\n9443947,별 반개도 아깝다 욕나온다 이응경 길용우 연기생활이몇년인지정말 발로해도 그것보단 낫겟다 납치감금만반복반복이드라마는 가족도없다 연기못하는사람만모엿네,0\r\n7156791,액션이 없는데도 재미 있는 몇안되는 영화,1\r\n5912145,왜케 평점이 낮은건데 꽤 볼만한데 헐리우드식 화려함에만 너무 길들여져 있나,1\r\n9008700,걍인피니트가짱이다진짜짱이다,1\r\n10217543,볼때마다 눈물나서 죽겠다년대의 향수자극허진호는 감성절제멜로의 달인이다,1\r\n5957425,울면서 손들고 횡단보도 건널때 뛰쳐나올뻔 이범수 연기 드럽게못해,0\r\n8628627,담백하고 깔끔해서 좋다 신문기사로만 보다 보면 자꾸 잊어버린다 그들도 사람이었다는 것을,1\r\n9864035,취향은 존중한다지만 진짜 내생에 극장에서 본 영화중 가장 노잼 노감동임 스토리도 어거지고 감동도 어거지,0\r\n6852435,ㄱ냥 매번 긴장되고 재밋음ㅠㅠ,1\r\n9143163,참 사람들 웃긴게 바스코가 이기면 락스코라고 까고바비가 이기면 아이돌이라고 깐다그냥 까고싶어서 안달난것처럼 보인다,1\r\n4891476,굿바이 레닌 표절인것은 이해하는데 왜 뒤로 갈수록 재미없어지냐,0\r\n7465483,이건 정말 깨알 캐스팅과 질퍽하지않은 산뜻한 내용구성이 잘 버무러진 깨알일드,1\r\n3989148,약탈자를 위한 변

## 정수 인코딩

기계가 텍스트를 숫자로 처리할 수 있도록 훈련 데이터와 테스트 데이터에 정수 인코딩을 수행, 훈련 데이터에 대해서 단어 집합(vocaburary) 만들기

[TORCHTEXT 라이브러리로 텍스트 분류하기](https://tutorials.pytorch.kr/beginner/text_sentiment_ngrams_tutorial.html)

[네이버 리뷰 분류 KoBERT](https://colab.research.google.com/github/SKTBrain/KoBERT/blob/master/scripts/NSMC/naver_review_classifications_pytorch_kobert.ipynb#scrollTo=-snap20SPHgf)